In [82]:
import configparser
import csv
from collections import Counter
import nbimporter
import nltk
from nltk.tokenize import word_tokenize
import numpy as np
import math

### Lendo arquivo de configuração

In [83]:
import ast

In [84]:
config = configparser.ConfigParser()
config.read('BUSCA.cfg')

modelo_path = config.get('DEFAULT', 'MODELO')

modelo_vetorial = {}
with open(modelo_path, newline='') as csvfile:
    reader = csv.reader(csvfile, delimiter=';')
    
    for row in reader:
        key_str = row[0].replace("(", "").replace(")", "")
        key_tuple = tuple(ast.literal_eval(key_str))
        value = float(row[1])
        
        modelo_vetorial[key_tuple] = value

consultas_path = config.get('DEFAULT', 'CONSULTAS')
results_path = config.get('DEFAULT', 'RESULTADOS')

In [85]:
queries = {}

try:
    with open(consultas_path, "r") as file:
        csv_reader = csv.reader(file, delimiter=';')
        next(csv_reader, csv_reader)

        for row in csv_reader:
            query_num = row[0]
            query_text = row[1]
            queries[query_num] = query_text
except Exception as e:
    print(f"Erro ao ler o arquivo: {e}")

In [86]:
queries

{'00001': 'WHAT ARE THE EFFECTS OF CALCIUM ON THE PHYSICAL PROPERTIES OF MUCUS FROM CF PATIENTS',
 '00002': 'CAN ONE DISTINGUISH BETWEEN THE EFFECTS OF MUCUS HYPERSECRETION AND INFECTION ON THE SUBMUCOSAL GLANDS OF THE RESPIRATORY TRACT IN CF',
 '00003': 'HOW ARE SALIVARY GLYCOPROTEINS FROM CF PATIENTS DIFFERENT FROM THOSE OF NORMAL SUBJECTS',
 '00004': 'WHAT IS THE LIPID COMPOSITION OF CF RESPIRATORY SECRETIONS',
 '00005': 'IS CF MUCUS ABNORMAL',
 '00006': 'WHAT IS THE EFFECT OF WATER OR OTHER THERAPEUTIC AGENTS ON THE PHYSICAL PROPERTIES VISCOSITY ELASTICITY OF SPUTUM OR BRONCHIAL SECRETIONS FROM CF PATIENTS',
 '00007': 'ARE MUCUS GLYCOPROTEINS DEGRADED DIFFERENTLY IN CF PATIENTS AS COMPARED TO THOSE FROM NORMAL SUBJECTS',
 '00008': 'WHAT HISTOCHEMICAL DIFFERENCES HAVE BEEN DESCRIBED BETWEEN NORMAL AND CF RESPIRATORY EPITHELIA',
 '00009': 'WHAT IS THE ASSOCIATION BETWEEN LIVER DISEASE CIRRHOSIS AND VITAMIN A METABOLISM IN CF',
 '00010': 'WHAT IS THE ROLE OF VITAMIN E IN THE THERAPY O

In [87]:
modelo_vetorial

{('00001 ', 'SIGNIFICANCE'): 0.04154799294201786,
 ('00074 ', 'SIGNIFICANCE'): 0.08781734871835592,
 ('00078 ', 'SIGNIFICANCE'): 0.07576398712956198,
 ('00121 ', 'SIGNIFICANCE'): 0.034194365872634164,
 ('00147 ', 'SIGNIFICANCE'): 0.04067329835376485,
 ('00157 ', 'SIGNIFICANCE'): 0.14310975346695037,
 ('00179', 'SIGNIFICANCE'): 0.034194365872634164,
 ('00185', 'SIGNIFICANCE'): 0.028621950693390078,
 ('00195', 'SIGNIFICANCE'): 0.0536661575501064,
 ('00205', 'SIGNIFICANCE'): 0.03018721362193485,
 ('00223', 'SIGNIFICANCE'): 0.058544899145570616,
 ('00258', 'SIGNIFICANCE'): 0.019514966381856874,
 ('00319', 'SIGNIFICANCE'): 0.052215720859562983,
 ('00355', 'SIGNIFICANCE'): 0.04246113564404023,
 ('00402 ', 'SIGNIFICANCE'): 0.12879877812025536,
 ('00411 ', 'SIGNIFICANCE'): 0.031933581352129425,
 ('00412 ', 'SIGNIFICANCE'): 0.08221198603420554,
 ('00485 ', 'SIGNIFICANCE'): 0.0633436613706174,
 ('00526 ', 'SIGNIFICANCE'): 0.0330253277231424,
 ('00555 ', 'SIGNIFICANCE'): 0.06899934542156537,
 ('0

In [88]:
%store -r li
li

{'SIGNIFICANCE': ['00001 ',
  '00074 ',
  '00078 ',
  '00121 ',
  '00147 ',
  '00157 ',
  '00179',
  '00185',
  '00195',
  '00205',
  '00223',
  '00258',
  '00319',
  '00355',
  '00402 ',
  '00411 ',
  '00412 ',
  '00485 ',
  '00526 ',
  '00555 ',
  '00593 ',
  '00631 ',
  '00809 ',
  '00858 ',
  '00923 ',
  '01151 '],
 'PSEUDOMONAS': ['00001 ',
  '00001 ',
  '00001 ',
  '00007 ',
  '00008 ',
  '00018 ',
  '00018 ',
  '00061 ',
  '00061 ',
  '00062 ',
  '00062 ',
  '00062 ',
  '00062 ',
  '00062 ',
  '00079 ',
  '00080 ',
  '00081 ',
  '00081 ',
  '00081 ',
  '00081 ',
  '00082 ',
  '00082 ',
  '00082 ',
  '00123 ',
  '00123 ',
  '00123 ',
  '00135 ',
  '00148 ',
  '00152 ',
  '00159 ',
  '00160 ',
  '00161 ',
  '00176',
  '00177',
  '00177',
  '00178',
  '00188',
  '00188',
  '00188',
  '00188',
  '00200',
  '00200',
  '00250',
  '00260',
  '00265',
  '00271',
  '00282',
  '00282',
  '00384 ',
  '00384 ',
  '00394 ',
  '00427 ',
  '00427 ',
  '00447 ',
  '00458 ',
  '00459 ',
  '00460

In [89]:
%store -r n_words
%store -r li
N = len(n_words.keys())

In [90]:
modelo_vetorial

{('00001 ', 'SIGNIFICANCE'): 0.04154799294201786,
 ('00074 ', 'SIGNIFICANCE'): 0.08781734871835592,
 ('00078 ', 'SIGNIFICANCE'): 0.07576398712956198,
 ('00121 ', 'SIGNIFICANCE'): 0.034194365872634164,
 ('00147 ', 'SIGNIFICANCE'): 0.04067329835376485,
 ('00157 ', 'SIGNIFICANCE'): 0.14310975346695037,
 ('00179', 'SIGNIFICANCE'): 0.034194365872634164,
 ('00185', 'SIGNIFICANCE'): 0.028621950693390078,
 ('00195', 'SIGNIFICANCE'): 0.0536661575501064,
 ('00205', 'SIGNIFICANCE'): 0.03018721362193485,
 ('00223', 'SIGNIFICANCE'): 0.058544899145570616,
 ('00258', 'SIGNIFICANCE'): 0.019514966381856874,
 ('00319', 'SIGNIFICANCE'): 0.052215720859562983,
 ('00355', 'SIGNIFICANCE'): 0.04246113564404023,
 ('00402 ', 'SIGNIFICANCE'): 0.12879877812025536,
 ('00411 ', 'SIGNIFICANCE'): 0.031933581352129425,
 ('00412 ', 'SIGNIFICANCE'): 0.08221198603420554,
 ('00485 ', 'SIGNIFICANCE'): 0.0633436613706174,
 ('00526 ', 'SIGNIFICANCE'): 0.0330253277231424,
 ('00555 ', 'SIGNIFICANCE'): 0.06899934542156537,
 ('0

In [91]:
def vms(tfidf, query):
    query_tokens = [token.upper() for token in word_tokenize(query) if token not in nltk.corpus.stopwords.words('english')]
    query_weights = {}
    docs_weights = {}
    D = {}
    dot_QD = {}
    q_d_vec_diffs = {}

    tf_query = Counter(query_tokens)

    # compute each token weight with respect to the QUERY
    for token in query_tokens:
        tf = tf_query[token] / len(query_tokens)
        if token in li.keys():
            idf = N / len(set(li[token]))
        else:
            idf = 0
        query_weights[token] = tf * idf

    # compute each token weight with respect to EACH DOCUMENT
    for (doc_id, token), weight in tfidf.items():
        if token in query_tokens:
            if doc_id not in docs_weights:
                docs_weights[doc_id] = []
            docs_weights[doc_id].append((token, weight))
            
    for doc_id, token_weight_list in docs_weights.items():
    # sorting docs_weight
        docs_weights[doc_id] = sorted(token_weight_list)

    for doc_id, token_weight_list in docs_weights.items():
        common_QD_tokens = sorted(token for (token, _) in token_weight_list if token in query_weights.keys())
        qw_vector = np.array([query_weights[token] for token in common_QD_tokens])

        # create document vector containing weights for common tokens
        doc_vector = np.array([weight for token, weight in token_weight_list if token in common_QD_tokens])
        
        
        sum_of_squares = sum(dw**2 for _, dw in token_weight_list)
        D[doc_id] = math.sqrt(sum_of_squares)

        # compute scalar products of Query weights vector with each document weights vector
        dot_QD[doc_id] = np.dot(qw_vector, doc_vector)
        q_d_vec_diffs[doc_id] = qw_vector - doc_vector
    Q = math.sqrt(sum([qw**2 for qw in query_weights.values()]))
    return dot_QD, Q, D, q_d_vec_diffs

In [92]:
dot_query = {}
Q_query = {}
D_query = {}
vec_diffs_query = {}

for id, query in queries.items():
    (dot_query[id], Q_query[id], D_query[id], vec_diffs_query[id]) = vms(modelo_vetorial, query)

In [93]:
def cosine_similarity(dot_products, qw_vector_mag, dw_vector_mag):
    cs_docs = {}

    for (id, dps) in dot_products.items():
        for doc_id, dp in dps.items():
            if id not in cs_docs:
                cs_docs[id] = []
            
            cs_docs[id].append((doc_id, dps[doc_id] / (qw_vector_mag[id] * (dw_vector_mag[id])[doc_id])))
    return cs_docs
    

In [94]:
similarities = cosine_similarity(dot_query, Q_query, D_query)
similarities

{'00001': [('00003 ', 0.06186459896893787),
  ('00004 ', 0.06186459896893786),
  ('00011 ', 0.31091189726339113),
  ('00013 ', 0.06186459896893786),
  ('00018 ', 0.06186459896893787),
  ('00031 ', 0.06186459896893787),
  ('00033 ', 0.06186459896893787),
  ('00038 ', 0.06186459896893786),
  ('00039 ', 0.06186459896893786),
  ('00052 ', 0.6681719365152421),
  ('00055 ', 0.061864598968937874),
  ('00059 ', 0.06186459896893787),
  ('00062 ', 0.06186459896893786),
  ('00063 ', 0.06186459896893787),
  ('00074 ', 0.06186459896893787),
  ('00083 ', 0.06186459896893786),
  ('00085 ', 0.06186459896893786),
  ('00089 ', 0.061864598968937874),
  ('00122 ', 0.06186459896893787),
  ('00124 ', 0.06186459896893786),
  ('00126 ', 0.06186459896893786),
  ('00137 ', 0.06186459896893786),
  ('00139 ', 0.6594263635001715),
  ('00140 ', 0.06186459896893786),
  ('00141 ', 0.061864598968937874),
  ('00142 ', 0.06186459896893787),
  ('00143 ', 0.06186459896893787),
  ('00144 ', 0.061864598968937874),
  ('00147

In [95]:
vec_diffs_query

{'00001': {'00003 ': array([0.12584966]),
  '00004 ': array([0.16197703]),
  '00011 ': array([0.13228887, 2.12901147]),
  '00013 ': array([0.14103422]),
  '00018 ': array([0.18444649]),
  '00031 ': array([0.20110214]),
  '00033 ': array([0.18018203]),
  '00038 ': array([0.15297162]),
  '00039 ': array([0.14615956]),
  '00052 ': array([2.45048607, 0.20858887]),
  '00055 ': array([0.13577081]),
  '00059 ': array([0.17157767]),
  '00062 ': array([0.20387637]),
  '00063 ': array([0.16140778]),
  '00074 ': array([0.17074853]),
  '00083 ': array([0.20408023]),
  '00085 ': array([0.19035541]),
  '00089 ': array([0.20504637]),
  '00122 ': array([0.19138244]),
  '00124 ': array([0.16519324]),
  '00126 ': array([0.17965395]),
  '00137 ': array([0.18136892]),
  '00139 ': array([2.35604845, 0.16849639]),
  '00140 ': array([0.12272827]),
  '00141 ': array([0.1765622]),
  '00142 ': array([0.17929512]),
  '00143 ': array([0.19138244]),
  '00144 ': array([0.17429445]),
  '00147 ': array([2.46486659, 0

In [103]:
def get_results(cs):
    ranked_docs = {}
    winning_docs = {}

    for id, docs_cs in cs.items():
        ranked_docs[id] = list(sorted(docs_cs, key=lambda x: x[1], reverse=True))

    winning_docs = {key: value[:10] for key, value in ranked_docs.items()}
    return winning_docs

    

In [104]:
results = get_results(similarities)

In [105]:
results

{'00001': [('00533 ', 0.9662811821048936),
  ('00441 ', 0.7689319880207428),
  ('00957 ', 0.7344185787741998),
  ('00827 ', 0.7046231645892093),
  ('00522 ', 0.6868886745763042),
  ('00789 ', 0.6842599582927976),
  ('01193 ', 0.6842599582927976),
  ('00040 ', 0.6842599582927975),
  ('00303', 0.6842599582927975),
  ('00435 ', 0.6842599582927975)],
 '00002': [('01125 ', 0.6772235785770886),
  ('00137 ', 0.6132964199175064),
  ('00666 ', 0.37132293009226197),
  ('00107 ', 0.3713229300922619),
  ('00301', 0.36694737561932217),
  ('00225', 0.3581079473095234),
  ('01137 ', 0.33880830867683953),
  ('00095 ', 0.3249075638307292),
  ('00498 ', 0.31021881788021066),
  ('00114 ', 0.30137953779140153)],
 '00003': [('00515 ', 0.9925126638359466),
  ('01199 ', 0.9500145140610142),
  ('01121 ', 0.9494740928268659),
  ('00635 ', 0.949417116499775),
  ('00077 ', 0.9488681114065991),
  ('00345', 0.9471880915594478),
  ('00309', 0.9461074663209352),
  ('00505 ', 0.9461074663209352),
  ('00615 ', 0.94610

In [109]:
with open(results_path, 'w', newline='') as csvfile:
    csvwriter = csv.writer(csvfile, delimiter=';')

    for query, tuples_list in results.items():
        for position, (doc, score) in enumerate(tuples_list, start=1):
            csvwriter.writerow([query, [position, doc, score]])
